## Data Science Discovering Structure and Opportunity via Network Modeling 
![](images/twittercloud.jpg)

In [1]:
#!pip uninstall visJS2Jupyter -y

In [2]:
#!pip install git+https://github.com/albre116/visJS2jupyter

In [3]:
###lets take a peek 
import requests
import html
import subprocess
from IPython.display import display, HTML, IFrame

Actor1 = "flexport"
html_template = html.escape(requests.get('https://twitter.com/{}'.format(Actor1)).text)
display(HTML("<iframe srcdoc='{}' height='600' width='1000'>".format(html_template)))

## What the profile page looks like to a computer using API (Application Programming Interface)

In [4]:

###get profile page
import sys
import os
import importlib
sys.path.insert(0,"twitterpackage/Chap02_03")
#print(sys.path)
#print(os.environ)

from twitter_client import get_twitter_client
import json
client = get_twitter_client()
profile = client.get_user(screen_name=Actor1)
print(json.dumps(profile._json, indent =4))

{
    "id": 1385647819,
    "id_str": "1385647819",
    "name": "Flexport",
    "screen_name": "flexport",
    "location": "San Francisco",
    "profile_location": null,
    "description": "First to market with a purpose-built cloud software and data analytics platform, Flexport is the modern freight forwarder.",
    "url": "https://t.co/nMwbrceaLQ",
    "entities": {
        "url": {
            "urls": [
                {
                    "url": "https://t.co/nMwbrceaLQ",
                    "expanded_url": "http://Flexport.com",
                    "display_url": "Flexport.com",
                    "indices": [
                        0,
                        23
                    ]
                }
            ]
        },
        "description": {
            "urls": []
        }
    },
    "protected": false,
    "followers_count": 6145,
    "friends_count": 516,
    "listed_count": 150,
    "created_at": "Sat Apr 27 22:56:16 +0000 2013",
    "favourites_count": 3660,
    "

## Lets look at some basic questions
* ### What topics are being Tweeted on the Front page this year?
* ### How Wide is the Social Media Reach?
* ### Who are the influencers in the social media network?


In [5]:
#cmd = "python twitterpackage/Chap02_03/twitter_get_user.py {}".format(Actor1)
#print(subprocess.check_output(cmd, shell=True).decode())

#cmd = "python ./twitterpackage/Chap02_03/twitter_get_user_timeline_daterange.py --username {} --startdate {}".format(Actor1,"2018-01-01")
#print(subprocess.check_output(cmd, shell=True).decode())

In [6]:
print("what hashtag topics are on {}'s mind?".format(Actor1))
cmd = "python twitterpackage/Chap02_03/twitter_hashtag_frequency.py user_timeline_{}.jsonl".format(Actor1)
print(subprocess.check_output(cmd, shell=True).decode())


what hashtag topics are on flexport's mind?
tariffs: 4
shoptalk2018: 3
freight: 2
logistics: 2
modexshow: 2
gasummit18: 2
tariff: 1
customs: 1
imo2020: 1
pledge1: 1
linkedintopstartups: 1
tradewar: 1
typhoonmaria: 1
whitehouse: 1
consumergoods: 1
humanitarianaid: 1
bestplacestowork2018: 1
fulfillmentbyamazon: 1
amazonprimeday: 1
fba: 1
airfreight: 1
forbesu30asia: 1
brotopia: 1
theclimatecollaborative: 1
climateday2018: 1
tpm2018: 1



In [7]:
print("What do the follower statistics look like for {}?".format(Actor1))
cmd = "python twitterpackage/Chap02_03/twitter_followers_stats.py {}".format(Actor1)
print(subprocess.check_output(cmd, shell=True).decode())

What do the follower statistics look like for flexport?
----- Timing -----
Initialize data: 0.22814130783081055
Set-based operations: 0.09485244750976562
Total time: 0.32299375534057617
----- Stats -----
flexport has 6142 followers
flexport has 516 friends
flexport has 161 mutual friends
355 friends are not following flexport back
5981 followers are not followed back by flexport
Some mutual friends: theloadstar, benkaufman, winklevoss, Splash_247, LogTechEric



In [8]:
###lets get all mutual friends (only run once)
# print("Lets pull the mutual friends for {}".format(Actor1))
# cmd = "python twitterpackage/Chap02_03/twitter_mutual_friend_followers.py {}".format(Actor1)
# print(subprocess.check_output(cmd, shell=True).decode())

In [9]:
####Generate Mutual Friend Network
####These are the interconnections
import os
import sys
import json
import time
import math
from tweepy import Cursor
from twitter_client import get_twitter_client
import sys
import json
from random import sample
import sys
import json
from operator import itemgetter
import networkx as nx
import matplotlib.pyplot as plt
import urllib
import requests
import html
import numpy as np

Refresh = True
Target = Actor1
if Refresh == True:
    followers_file = 'users/{}/followers.jsonl'.format(Target)
    friends_file = 'users/{}/friends.jsonl'.format(Target)
    with open(followers_file) as f1, open(friends_file) as f2:
        t0 = time.time()
        followers = []
        friends = []
        for line in f1:
            profile = json.loads(line)
            followers.append(profile['screen_name'])
        for line in f2:
            profile = json.loads(line)
            friends.append(profile['screen_name'])
        t1 = time.time()
        mutual_friends = [user for user in friends if user in followers]
        followers_not_following = [user for user in followers if user not in friends]
        friends_not_following = [user for user in friends if user not in followers]
        t2 = time.time()
        print("Building Mutual Friend Network for {} Who Has {} Mutual Friends".format(Target, len(mutual_friends)))

    #mutual_friends = mutual_friends[:5]
    G = nx.DiGraph()
    for mutual in mutual_friends:
        #G.add_edge(screen_name,mutual)
        #G.add_edge(mutual,screen_name)
        G.add_node(mutual)

    ###Link the mutual friends network
    for mutual in mutual_friends:
        screen_name = mutual
        followers_file = 'users/{}/followers.jsonl'.format(screen_name)
        friends_file = 'users/{}/friends.jsonl'.format(screen_name)
        try:
            with open(followers_file) as f1, open(friends_file) as f2:
                followers = []
                friends = []
                for line in f1:
                    profile = json.loads(line)
                    followers.append(profile['screen_name'])
                ###Add to the NetworkX Graph those that are connected
                followers_in_network = list(set(followers).intersection(mutual_friends))
                for u in followers_in_network:
                    G.add_edge(u,screen_name)
                print("{} followers in network for {}".format(len(followers_in_network),screen_name))

                for line in f2:
                    profile = json.loads(line)
                    friends.append(profile['screen_name'])
                ###Add to the NetworkX Graph those that are connected
                friends_in_network = list(set(friends).intersection(mutual_friends))
                for u in friends_in_network:
                    G.add_edge(screen_name,u)
                print("{} friends in network for {}".format(len(friends_in_network),screen_name))
                
                ### We can cut this down to just those whom are mutual for this analysis
                #mutual_friends_subordinate = [user for user in friends if user in followers]
                #mutual_friends_in_network = list(set(mutual_friends_subordinate).intersection(mutual_friends))
                #for u in mutual_friends_in_network:
                #    G.add_edge(screen_name,u)
                #print("{} mutual friends in network for {}".format(len(mutual_friends_in_network),screen_name))
                
        except OSError:
            print("no file there for {}, removing node".format(screen_name))
            G.remove_node(screen_name)
    nx.write_gpickle(G,"networkX{}.gpickle".format(Target))
else:
    G = nx.read_gpickle("networkX{}.gpickle".format(Target))


Building Mutual Friend Network for flexport Who Has 161 Mutual Friends
7 followers in network for everydayeddie
10 friends in network for everydayeddie
0 followers in network for InturnHQ
2 friends in network for InturnHQ
7 followers in network for eytand
3 friends in network for eytand
3 followers in network for justinfschafer
5 friends in network for justinfschafer
3 followers in network for OwenMillard
4 friends in network for OwenMillard
2 followers in network for bridgalexandra
4 friends in network for bridgalexandra
7 followers in network for HamGarrison
23 friends in network for HamGarrison
0 followers in network for dcower
3 friends in network for dcower
18 followers in network for FlexportEng
12 friends in network for FlexportEng
10 followers in network for _StephanieYHe
19 friends in network for _StephanieYHe
10 followers in network for stopman
10 friends in network for stopman
7 followers in network for derektli
22 friends in network for derektli
1 followers in network for o

30 followers in network for MarkSzakonyi
15 friends in network for MarkSzakonyi
15 followers in network for MarshSalisbury
20 friends in network for MarshSalisbury
28 followers in network for PaulPage
24 friends in network for PaulPage
0 followers in network for drobo
2 friends in network for drobo
25 followers in network for dmnd_
46 friends in network for dmnd_
3 followers in network for LouisColumbus
6 friends in network for LouisColumbus
7 followers in network for jiyannnwei
7 friends in network for jiyannnwei
6 followers in network for ShippingWatch
0 friends in network for ShippingWatch
0 followers in network for yuris
0 friends in network for yuris
0 followers in network for SupplyChain247
0 friends in network for SupplyChain247
46 followers in network for _slinehan
33 friends in network for _slinehan
1 followers in network for tylerwinklevoss
14 friends in network for tylerwinklevoss
2 followers in network for winklevoss
11 friends in network for winklevoss
9 followers in netwo

# Lets first look at the "hairball of connections"

In [10]:
import matplotlib as mpl
import visJS2jupyter.visJS_module
displaylabel = {n:'@' + n for n in G.nodes()}
#Create network layout for visualizations
pos = nx.spring_layout(G , scale= 1)
#plt.axis("off")
#nx.draw_networkx(G, pos = pos, with_labels = False, arrows=False, node_size = 35)


Gplot = G.copy()

pctplot = 1
for k,v in G.degree:
    tmp = G.edges(nbunch=[k])
    ns = int(len(tmp)*(1-pctplot))
    if ns > 0:
        yank = np.random.choice(range(len(tmp)),ns,replace=False)
    else:
        yank = list()
    tmpp = list(tmp)
    Gplot.remove_edges_from([tmpp[i] for i in yank])


nodes = Gplot.nodes()
edges = list(Gplot.edges())
nodes_dict = [{"id":n,
               "color":'black',
              "title": displaylabel[n],
               "displaylabel":n,
              "x":pos[n][0]*1000,
              "y":pos[n][1]*1000} for n in nodes
              ]
node_map = dict(zip(nodes,range(len(nodes))))  # map to indices for source/target in edges

edges_dict = [{"source":node_map[edges[i][0]], 
               "target":node_map[edges[i][1]], 
              "color":"gray"
              } for i in range(len(edges))]

# set some network-wide styles
NodeGraph = visJS2jupyter.visJS_module.visjs_network(nodes_dict,edges_dict,
                          node_label_field='displaylabel',
                          node_size_multiplier=10,
                          node_size_transform = '',
                          node_color_highlight_border='red',
                          node_color_highlight_background='#D3918B',
                          node_color_hover_border='blue',
                          node_color_hover_background='#8BADD3',
                          node_font_size=25,
                          edge_arrow_to=False,
                          physics_enabled=True,
                          edge_color_highlight='#8A324E',
                          edge_color_hover='#8BADD3',
                          edge_label_field='label',
                          edge_title_field='title',
                          edge_width=3,
                          max_velocity=15,
                          min_velocity=1,
                          drag_view = True,
                          graph_id = 1)

NodeGraph

# Lets find the Top X influencers in the Graph
- betweenness centrality identifies those that have the most direct connections passing through them between actors

In [11]:
###lets find the most central 5 members in the network
###using betweenness centrality
bt = nx.betweenness_centrality(G)
nx.set_node_attributes(G, name='betweenness', values=bt)
nx.set_node_attributes(G, name='size', values=5)
nx.set_node_attributes(G, name='color', values="black")

###number of influencers to identify
top = 5
max_nodes =  sorted(bt.items(), key = lambda v: -v[1])[:top]

influencerlabel = displaylabel.copy()

for max_key, max_val in max_nodes:
    G.node[max_key]['size'] = 15
    G.node[max_key]['color'] = 'yellow'
    html_template = html.escape(requests.get('https://twitter.com/{}'.format(max_key)).text)
    influencerlabel[max_key] = "<iframe srcdoc='{}' height='600' width='800'>".format(html_template)
    

color = nx.get_node_attributes(G,'color')
size = nx.get_node_attributes(G,'size')

Gplot = G.copy()

pctplot = 1
for k,v in G.degree:
    tmp = G.edges(nbunch=[k])
    ns = int(len(tmp)*(1-pctplot))
    if ns > 0:
        yank = np.random.choice(range(len(tmp)),ns,replace=False)
    else:
        yank = list()
    tmpp = list(tmp)
    Gplot.remove_edges_from([tmpp[i] for i in yank])

nodes = Gplot.nodes()
edges = list(Gplot.edges())
nodes_dict = [{"id":n,
               "color":color[n],
              "title": influencerlabel[n],
              #"displaylabel":n,
              "degree":size[n],
              "x":pos[n][0]*1000,
              "y":pos[n][1]*1000} for n in nodes
              ]
node_map = dict(zip(nodes,range(len(nodes))))  # map to indices for source/target in edges

edges_dict = [{"source":node_map[edges[i][0]], 
               "target":node_map[edges[i][1]], 
              "color":"gray"
              } for i in range(len(edges))]

# set some network-wide styles
NodeGraphInfluencer = visJS2jupyter.visJS_module.visjs_network(nodes_dict,edges_dict,
                          tooltip_delay=300,
                          node_label_field='displaylabel',
                          node_size_multiplier=10,
                          node_color_highlight_border='red',
                          node_color_highlight_background='#D3918B',
                          node_color_hover_border='blue',
                          node_color_hover_background='#8BADD3',
                          node_font_size=25,
                          edge_arrow_to=False,
                          physics_enabled=True,
                          edge_color_highlight='#8A324E',
                          edge_color_hover='#8BADD3',
                          edge_label_field='label',
                          edge_title_field='title',
                          edge_width=3,
                          max_velocity=15,
                          min_velocity=1,
                          graph_id = 2)

NodeGraphInfluencer

# Lets Identify Community Structure of Interconnected Networks
- Compares within community connection density to outside community connection density

In [12]:
import community

Gc = G.to_undirected()
parts = community.best_partition(Gc)
ranges = list(set([parts.get(node) for node in Gc.nodes()]))

nx.set_node_attributes(Gc, name='community', values=parts)
nx.set_node_attributes(Gc, name='size', values=5)

influencerlabel = displaylabel.copy()
for c in ranges:
    bunches = [k for k,v in nx.get_node_attributes(Gc,name='community').items() if v == c]
    if len(bunches) > 1:
        bt = nx.betweenness_centrality(G.subgraph(bunches))
        ###number of influencers to identify
        top = 1
        max_nodes =  sorted(bt.items(), key = lambda v: -v[1])[:top]
        for max_key, max_val in max_nodes:
            Gc.node[max_key]['size'] = 15
            Gc.node[max_key]['color'] = 'yellow'
            html_template = html.escape(requests.get('https://twitter.com/{}'.format(max_key)).text)
            influencerlabel[max_key] = "<iframe srcdoc='{}' height='600' width='800'>".format(html_template)

color = visJS2jupyter.visJS_module.return_node_to_color(Gc,field_to_map='community',cmap=plt.get_cmap("Spectral"))

size = nx.get_node_attributes(Gc,'size')

Gplot = Gc.copy()

pctplot = 1
for k,v in G.degree:
    tmp = G.edges(nbunch=[k])
    ns = int(len(tmp)*(1-pctplot))
    if ns > 0:
        yank = np.random.choice(range(len(tmp)),ns,replace=False)
    else:
        yank = list()
    tmpp = list(tmp)
    Gplot.remove_edges_from([tmpp[i] for i in yank])

nodes = Gplot.nodes()
edges = list(Gplot.edges())

nodes_dict = [{"id":n,
               "color":color[n],
              "title": influencerlabel[n],
              #"displaylabel":n,
              "degree":size[n],
              "x":pos[n][0]*1000,
              "y":pos[n][1]*1000} for n in nodes
              ]
node_map = dict(zip(nodes,range(len(nodes))))  # map to indices for source/target in edges

edges_dict = [{"source":node_map[edges[i][0]], 
               "target":node_map[edges[i][1]], 
              "color":"gray"
              } for i in range(len(edges))]

# set some network-wide styles
NodeGraphInfluencer = visJS2jupyter.visJS_module.visjs_network(nodes_dict,edges_dict,
                           tooltip_delay=300,
                          node_label_field='displaylabel',
                          node_size_multiplier=10,
                          node_color_highlight_border='red',
                          node_color_highlight_background='#D3918B',
                          node_color_hover_border='blue',
                          node_color_hover_background='#8BADD3',
                          node_font_size=25,
                          edge_arrow_to=False,
                          physics_enabled=True,
                          edge_color_highlight='#8A324E',
                          edge_color_hover='#8BADD3',
                          edge_label_field='label',
                          edge_title_field='title',
                          edge_width=1,
                          max_velocity=15,
                          min_velocity=1,
                          graph_id = 3)

NodeGraphInfluencer